In [1]:
import pygame
import os
import time 
import random
from Render import render_board
import gymnasium as gym
from gymnasium import Env
from gymnasium import spaces
from collections import deque 
import tensorflow as tf 
from tensorflow import keras
from stable_baselines3 import PPO
import numpy as np
pygame.font.init()

pygame 2.6.1 (SDL 2.28.4, Python 3.9.21)
Hello from the pygame community. https://www.pygame.org/contribute.html


2025-02-08 11:36:55.177308: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-02-08 11:36:55.185029: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1739032615.193901  219637 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1739032615.196495  219637 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-02-08 11:36:55.206119: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

In [2]:
render_board.Global_Vars()
render_board.init_image_vars()

Render Images


In [3]:
def drawboard(A,N,NumsL,NumsI,NumsA):
    render_board.init_background()
    #self.Agent, self.Node = render_board.create_player_node(3,8)
    render_board.init_window(A,N)
    #Render The Links 
    for x in range(0,NumsL[0]):
        render_board.create_link(A[0],N[x])
    for x in range(NumsL[0],NumsL[1]+NumsL[0]):
        render_board.create_link(A[1],N[x])
    for x in range(NumsL[1]+NumsL[0],NumsL[2]+NumsL[1]+NumsL[0]):
        render_board.create_link(A[2],N[x])
    #Create the labels
    for x in range(0,len(NumsI)):
        render_board.create_text_label(N[x],str(NumsI[x]))
    for x in range(0,len(NumsA)):
        render_board.create_text_label(A[x],str(NumsA[x]))
    

In [4]:
def calc_scores(z1,z2,NumsA,NumsL,NumsM):
    z1 = []
    temp1 = NumsA[0]/NumsL[0]
    temp2 = NumsA[1]/NumsL[1]
    temp3 = NumsA[2]/NumsL[2]
    for x in range(0,NumsL[0]):
        z1.append(temp1)
        
    for x in range(NumsL[0],NumsL[0]+NumsL[1]):
        z1.append(temp2)
        
    for x in range(NumsL[1]+NumsL[0],NumsL[2]+NumsL[1]+NumsL[0]):
        z1.append(temp3)
    
    z2 = []
    for x in range(0,len(NumsM)):
        z2.append(NumsM[x] * z1[x])
    return z1,z2

def step_forward(z1,z2,NumsA,NumsL,NumsM):
###rand action
    StepVar = random.randint(0,2)
    if StepVar == 0:
        HSV = random.randint(1,2)
        if HSV == 1:
            if NumsA[0] != 0:
                NumsA[0] = NumsA[0] - 1
                NumsA[2] = NumsA[2] + 1
        if HSV == 2:
            if NumsA[2] != 0:
                NumsA[0] = NumsA[0] + 1
                NumsA[2] = NumsA[2] - 1
            
    if StepVar == 1:
        HSV = random.randint(1,2)
        if HSV == 1:
            if NumsA[1] != 0:
                NumsA[1] = NumsA[1] - 1
                NumsA[0] = NumsA[0] + 1
        if HSV == 2:
            if NumsA[0] != 0:
                NumsA[1] = NumsA[1] + 1
                NumsA[0] = NumsA[0] - 1

    if StepVar == 2:
        HSV = random.randint(1,2)
        if HSV == 1:
            if NumsA[2] != 0:
                NumsA[2] = NumsA[2] - 1
                NumsA[1] = NumsA[1] + 1
        if HSV == 2:
            if NumsA[1] != 0:
                NumsA[2] = NumsA[2] + 1
                NumsA[1] = NumsA[1] - 1
    z1, z2 = calc_scores(z1,z2,NumsA,NumsL,NumsM)
    return z1,z2,StepVar

class ABN_Game(Env):
    def __init__(self):
        self.NumsI = []
        self.NumsU = []
        self.NumsL = [2,4,2]
        self.NumsA = [6,3,1]
        self.NumsM = [2,1,2,2,1,1,2,2]
        self.reward = 0
        self.action_space = spaces.Discrete(3) # 3 actions
        self.state_space = spaces.Discrete(3) # States
        self.observation_space = spaces.Box(low=0, high=3.5, shape=(8,), dtype=np.float64) #space
        self.NumsI, self.NumsU = calc_scores(self.NumsI,self.NumsU,self.NumsA,self.NumsL,self.NumsM)
        self.NumsI, self.NumsU, self.state_space = step_forward(self.NumsI,self.NumsU,self.NumsA,self.NumsL,self.NumsM)
        self.count = 0
        self.Agent, self.Node = render_board.create_player_node(3,8)
        
    def step(self,action):
        
        #drawboard(self.Agent,self.Node,self.NumsL,self.NumsI,self.NumsA)
        
        
        if action == self.state_space :
            #render_board.green_shake_Agent(self.Agent[action])
            self.done = True
            self.trunc = True
            self.reward = self.reward + 1
            pygame.quit()
            #print('Passed', 'Action:', action , 'State:', self.state_space)
        else:
            #render_board.red_shake_Agent(self.Agent[action])
            self.done = False
            self.trunc = False
            self.reward = self.reward + -1
            self.count = self.count + 1
            #print('Failed', 'Action:', action , 'State:', self.state_space)
        
        self.observation = list(self.NumsI)
        self.observation = np.array(self.observation)
        self.observation = self.observation.astype(np.float32)
            
        if self.count >= 10:
            self.done = True
            pygame.quit()
            
        
        self.info = {}
        return self.observation, self.reward, self.done, self.trunc, self.info
        
    def render(self):
        pass
    
    def reset(self, seed=None):
        self.NumsI = []
        self.NumsU = []
        self.NumsL = [2,4,2]
        self.NumsA = [6,3,1]
        self.NumsM = [2,1,2,2,1,1,2,2]
        self.NumsI, self.NumsU = calc_scores(self.NumsI,self.NumsU,self.NumsA,self.NumsL,self.NumsM)
        self.NumsI, self.NumsU, self.state_space = step_forward(self.NumsI,self.NumsU,self.NumsA,self.NumsL,self.NumsM)
        self.reward = 0
        self.count = 0
        self.prev_action = []
        self.observation = list(self.NumsI)
        self.observation = np.array(self.observation)
        self.observation = self.observation.astype(np.float32)
        self.Agent, self.Node = render_board.create_player_node(3,8)
        info = {}
        return self.observation, info

In [5]:
env = ABN_Game()

In [6]:
episodes = 1 
for episode in range(episodes):
    done = False 
    obs = env.reset()
    while not done:
        action = env.action_space.sample()
        obs, reward, done,trunc, info = env.step(action)
    print('Reward: ', reward)

Reward:  -5


In [7]:
env.reset()
from stable_baselines3.common.env_checker import check_env
from stable_baselines3 import DQN
from stable_baselines3 import A2C
from sb3_contrib import ARS
from sb3_contrib import MaskablePPO
from sb3_contrib import RecurrentPPO
from sb3_contrib import QRDQN
from sb3_contrib import TRPO
from stable_baselines3 import PPO
check_env(env)

In [8]:
models_dir_A2C = f"models/A2C/{int(time.time())}/"
log_dir_A2C = f"logs/A2C/{int(time.time())}/"

if not os.path.exists(models_dir_A2C):
    os.makedirs(models_dir_A2C)
    
if not os.path.exists(log_dir_A2C):
    os.makedirs(log_dir_A2C)

models_dir_ARS = f"models/ARS/{int(time.time())}/"
log_dir_ARS = f"logs/ARS/{int(time.time())}/"

if not os.path.exists(models_dir_ARS):
    os.makedirs(models_dir_ARS)
    
if not os.path.exists(log_dir_ARS):
    os.makedirs(log_dir_ARS)

models_dir_MPPO = f"models/MPPO/{int(time.time())}/"
log_dir_MPPO = f"logs/MPPO/{int(time.time())}/"

if not os.path.exists(models_dir_MPPO):
    os.makedirs(models_dir_MPPO)
    
if not os.path.exists(log_dir_MPPO):
    os.makedirs(log_dir_MPPO)

models_dir_RPPO = f"models/RPPO/{int(time.time())}/"
log_dir_RPPO = f"logs/RPPO/{int(time.time())}/"

if not os.path.exists(models_dir_RPPO):
    os.makedirs(models_dir_RPPO)
    
if not os.path.exists(log_dir_RPPO):
    os.makedirs(log_dir_RPPO)

models_dir_QRDQN = f"models/QRDQN/{int(time.time())}/"
log_dir_QRDQN = f"logs/QRDQN/{int(time.time())}/"

if not os.path.exists(models_dir_QRDQN):
    os.makedirs(models_dir_QRDQN)
    
if not os.path.exists(log_dir_QRDQN):
    os.makedirs(log_dir_QRDQN)

models_dir_TRPO = f"models/TRPO/{int(time.time())}/"
log_dir_TRPO = f"logs/TRPO/{int(time.time())}/"

if not os.path.exists(models_dir_TRPO):
    os.makedirs(models_dir_TRPO)
    
if not os.path.exists(log_dir_TRPO):
    os.makedirs(log_dir_TRPO)     
    
models_dir = f"models/GMSG/{int(time.time())}/"
logdir = f"logs/GMSG/{int(time.time())}/"

if not os.path.exists(models_dir):
    os.makedirs(models_dir)
    
if not os.path.exists(logdir):
    os.makedirs(logdir)

In [24]:
####TESTINGBLOCK#####

GMSG_MODEL_PPO = PPO('MlpPolicy', env, verbose=1, tensorboard_log=logdir)
MODEL_A2C = A2C('MlpPolicy', env, verbose=1, tensorboard_log=log_dir_A2C)
MODEL_ARS = ARS('MlpPolicy', env, verbose=1, tensorboard_log=log_dir_ARS)
MODEL_MPPO = MaskablePPO('MlpPolicy', env, verbose=1, tensorboard_log=log_dir_MPPO)
MODEL_RPPO = RecurrentPPO('MlpLstmPolicy', env, verbose=1, tensorboard_log=log_dir_RPPO)
MODEL_QRDQN = QRDQN('MlpPolicy', env, verbose=1, tensorboard_log=log_dir_QRDQN)
MODEL_TRPO = TRPO('MlpPolicy', env, verbose=1, tensorboard_log=log_dir_TRPO)

TS = 100 * 1

print("\n =========STARTING PPO TRAINING========= \n")
iters = 0
while iters < 2:
    iters += 1
    GMSG_MODEL_PPO.learn(total_timesteps=TS, reset_num_timesteps=False, tb_log_name=f"PPO")
    GMSG_MODEL_PPO.save(f"{models_dir}/{TS*iters}")

    
print("\n =========STARTING A2C TRAINING========= \n")
iters = 0
while iters<2:
    iters += 1
    MODEL_A2C.learn(total_timesteps=TS, reset_num_timesteps=False, tb_log_name=f"A2C")
    MODEL_A2C.save(f"{models_dir_A2C}/{TS*iters}")


print("\n =========STARTING ARS TRAINING========= \n")
iters = 0
while iters<2:
    iters += 1
    MODEL_ARS.learn(total_timesteps=TS, reset_num_timesteps=False, tb_log_name=f"ARS")
    MODEL_ARS.save(f"{models_dir_ARS}/{TS*iters}")


print("\n =========STARTING RPPO TRAINING========= \n")
iters = 0
while iters<2:
    iters += 1
    MODEL_RPPO.learn(total_timesteps=TS, reset_num_timesteps=False, tb_log_name=f"RPPO")
    MODEL_RPPO.save(f"{models_dir_RPPO}/{TS*iters}")

    

print("\n =========STARTING QRDQN TRAINING========= \n")
iters = 0
while iters<2:
    iters += 1
    MODEL_QRDQN.learn(total_timesteps=TS, reset_num_timesteps=False, tb_log_name=f"QRDQN")
    MODEL_QRDQN.save(f"{models_dir_QRDQN}/{TS*iters}")

    
print("\n =========STARTING TRPO TRAINING========= \n")
iters = 0
while iters<2:
    iters += 1
    MODEL_TRPO.learn(total_timesteps=TS, reset_num_timesteps=False, tb_log_name=f"TRPO")
    MODEL_TRPO.save(f"{models_dir_TRPO}/{TS*iters}")


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.

 =========STARTING PPO TRAINING========= 

Logging to logs/GMSG/1706128698/PPO_0
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 2.83     |
|    ep_rew_mean     | -5.79    |
| time/              |          |
|    fps             | 1033     |
|    iterations      | 1        |
|    time_elapsed    |

In [ ]:
GMSG_MODEL_PPO = PPO('MlpPolicy', env, verbose=1, tensorboard_log=logdir)
MODEL_A2C = A2C('MlpPolicy', env, verbose=1, tensorboard_log=log_dir_A2C)
MODEL_ARS = ARS('MlpPolicy', env, verbose=1, tensorboard_log=log_dir_ARS)
MODEL_MPPO = MaskablePPO('MlpPolicy', env, verbose=1, tensorboard_log=log_dir_MPPO)
MODEL_RPPO = RecurrentPPO('MlpLstmPolicy', env, verbose=1, tensorboard_log=log_dir_RPPO)
MODEL_QRDQN = QRDQN('MlpPolicy', env, verbose=1, tensorboard_log=log_dir_QRDQN)
MODEL_TRPO = TRPO('MlpPolicy', env, verbose=1, tensorboard_log=log_dir_TRPO)

TS = 2048 * 100

print("\n =========STARTING PPO TRAINING========= \n")
iters = 0
while iters < 30:
    iters += 1
    GMSG_MODEL_PPO.learn(total_timesteps=TS, reset_num_timesteps=False, tb_log_name=f"PPO")
    GMSG_MODEL_PPO.save(f"{models_dir}/{TS*iters}")

    
print("\n =========STARTING A2C TRAINING========= \n")
iters = 0
while iters<30:
    iters += 1
    MODEL_A2C.learn(total_timesteps=TS, reset_num_timesteps=False, tb_log_name=f"A2C")
    MODEL_A2C.save(f"{models_dir_A2C}/{TS*iters}")


print("\n =========STARTING ARS TRAINING========= \n")
iters = 0
while iters<30:
    iters += 1
    MODEL_ARS.learn(total_timesteps=TS, reset_num_timesteps=False, tb_log_name=f"ARS")
    MODEL_ARS.save(f"{models_dir_ARS}/{TS*iters}")


print("\n =========STARTING RPPO TRAINING========= \n")
iters = 0
while iters<30:
    iters += 1
    MODEL_RPPO.learn(total_timesteps=TS, reset_num_timesteps=False, tb_log_name=f"RPPO")
    MODEL_RPPO.save(f"{models_dir_RPPO}/{TS*iters}")

    

print("\n =========STARTING QRDQN TRAINING========= \n")
iters = 0
while iters<30:
    iters += 1
    MODEL_QRDQN.learn(total_timesteps=TS, reset_num_timesteps=False, tb_log_name=f"QRDQN")
    MODEL_QRDQN.save(f"{models_dir_QRDQN}/{TS*iters}")

    
print("\n =========STARTING TRPO TRAINING========= \n")
iters = 0
while iters<30:
    iters += 1
    MODEL_TRPO.learn(total_timesteps=TS, reset_num_timesteps=False, tb_log_name=f"TRPO")
    MODEL_TRPO.save(f"{models_dir_TRPO}/{TS*iters}")





Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.

 =========STARTING PPO TRAINING========= 

Logging to logs/GMSG/1706128698/PPO_0
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 2.59     |
|    ep_rew_mean     | -4.02    |
| time/              |          |
|    fps             | 1128     |
|    iterations      | 1        |
|    time_elapsed    |